<a href="https://colab.research.google.com/github/shafayat1004/Data-Mining-Assignments/blob/main/Assignment%204.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# KMeans Clustering on MNIST Dataset
## 1910456 Mir Shafayat Ahmed                                                                                                     

In [1]:
import numpy as np
import pandas as pd
import struct
from array import array
from os.path  import join
import plotly.express as px
pd.set_option('display.max_rows', None)

# !mkdir mnist
# !cd mnist && mkdir t10k-images-idx3-ubyte
# !cd mnist && mkdir t10k-labels-idx1-ubyte
# !cd mnist && mkdir train-images-idx3-ubyte
# !cd mnist && mkdir train-labels-idx1-ubyte
# 
# !curl "https://raw.githubusercontent.com/shafayat1004/Data-Mining-Assignments/main/mnist/t10k-images-idx3-ubyte/t10k-images-idx3-ubyte" --output mnist/t10k-images-idx3-ubyte/t10k-images-idx3-ubyte
# 
# !curl "https://raw.githubusercontent.com/shafayat1004/Data-Mining-Assignments/main/mnist/t10k-labels-idx1-ubyte/t10k-labels-idx1-ubyte" --output mnist/t10k-labels-idx1-ubyte/t10k-labels-idx1-ubyte
# 
# !curl "https://raw.githubusercontent.com/shafayat1004/Data-Mining-Assignments/main/mnist/train-images-idx3-ubyte/train-images-idx3-ubyte" --output mnist/train-images-idx3-ubyte/train-images-idx3-ubyte
# 
# !curl "https://raw.githubusercontent.com/shafayat1004/Data-Mining-Assignments/main/mnist/train-labels-idx1-ubyte/train-labels-idx1-ubyte" --output mnist/train-labels-idx1-ubyte/train-labels-idx1-ubyte

divider = "--------------------------------------------------------------------------------------"

In [137]:
#
# MNIST Data Loader Class
#
class MnistDataloader(object):
    def __init__(
            self,
            training_images_filepath,
            training_labels_filepath,
            test_images_filepath,
            test_labels_filepath
    ):
        self.training_images_filepath = training_images_filepath
        self.training_labels_filepath = training_labels_filepath
        self.test_images_filepath     = test_images_filepath
        self.test_labels_filepath     = test_labels_filepath

    def read_images_labels(self, images_filepath, labels_filepath):
        labels = []

        with open(labels_filepath, 'rb') as file:
            magic, size = struct.unpack(">II", file.read(8))

            if magic != 2049:
                raise ValueError('Magic number mismatch, expected 2049, got {}'.format(magic))

            labels = array("B", file.read())

        with open(images_filepath, 'rb') as file:
            magic, size, rows, cols = struct.unpack(">IIII", file.read(16))

            if magic != 2051:
                raise ValueError('Magic number mismatch, expected 2051, got {}'.format(magic))

            image_data = array("B", file.read())

        images = []

        for i in range(size):
            images.append([0] * rows * cols)

        for i in range(size):
            img          = np.array(image_data[i * rows * cols:(i + 1) * rows * cols])
            images[i][:] = img

        return images, labels

    def load_data(self):
        train_images, train_labels = self.read_images_labels(self.training_images_filepath, self.training_labels_filepath)
        test_images,  test_labels  = self.read_images_labels(self.test_images_filepath,     self.test_labels_filepath)
        return (np.array(train_images), np.array(train_labels)), (np.array(test_images), np.array(test_labels))

In [2]:
def davies_bouldin_index(samples, cluster_affiliations, centroids):
    num_clusters = len(centroids)
    cluster_distances = np.array(
        [
            np.linalg.norm(
                samples[cluster_affiliations == cluster_idx] - centroids[cluster_idx],
                axis = 1,
            ).mean()
            for cluster_idx in range(num_clusters)
        ]
    )
    pairwise_distances = np.linalg.norm(centroids[:, np.newaxis] - centroids, axis = 2)
    cluster_similarity = \
        (cluster_distances[:, np.newaxis] + cluster_distances) \
        / pairwise_distances
    np.fill_diagonal(cluster_similarity, 0)
    return np.mean(np.max(cluster_similarity, axis=1))

def dunn_index(samples, cluster_affiliations, centroids):
    # calculating the inter-cluster distance matrix
    inter_cluster_dist = np.linalg.norm(centroids[:, np.newaxis] - centroids, axis = 2)
    # setting the diagonal elements to infinity to avoid self-comparison
    np.fill_diagonal(inter_cluster_dist, np.inf)
    # print("--------------------------------")
    # print ("Inter Cluster Distances =")
    # display(inter_cluster_dist)
    # print("--------------------------------")
    # finding the minimum inter-cluster distance
    min_inter_cluster_dist = np.min(inter_cluster_dist)

    # calculating the intra-cluster distance matrix
    intra_cluster_dist = np.zeros(10) # assuming 10 clusters
    for i in range(10):
        # finding the samples belonging to cluster i
        cluster_samples = samples[cluster_affiliations == i]
        # calculating the distance from each sample to the centroid of cluster i
        sample_dist = np.linalg.norm(cluster_samples - centroids[i], axis=1)
        # finding the maximum distance within cluster i
        intra_cluster_dist[i] = np.max(sample_dist)

    # finding the maximum intra-cluster distance
    max_intra_cluster_dist = np.max(intra_cluster_dist)

    # calculating the Dunn index
    dunn_index = min_inter_cluster_dist / max_intra_cluster_dist

    return dunn_index

def purity_score(true_labels, predicted_labels):
    contingency_matrix = np.dot(
        np.transpose(np.array([true_labels])), np.array([predicted_labels])
    )
    return np.sum(np.max(contingency_matrix, axis=0)) / len(true_labels)

def rand_index(true_labels, predicted_labels):
    num_samples = len(true_labels)
    tp = tn = fp = fn = 0
    
    for i in range(num_samples):
        for j in range(i+1, num_samples):
            same_true = (true_labels[i] == true_labels[j])
            same_pred = (predicted_labels[i] == predicted_labels[j])

            if same_true and same_pred:
                tp += 1
            elif same_true and not same_pred:
                fn += 1
            elif not same_true and same_pred:
                fp += 1
            else:
                tn += 1

    # calculate the Rand index
    rand_index = (tp + tn) / (tp + fp + fn + tn)

    return rand_index


simple centroid initialization function

In [3]:
def initialize_centroids_simple(data, dimension_of_data, no_of_clusters):
    #centroids: [[centroid0:  3 dimensions, , , ]; [centroid1: 3 dimensions ] ... ..]
    centroids = np.zeros((no_of_clusters, dimension_of_data))
    
    random_indexes = np.random.permutation(len(data))                                                # Selecting random data points for each initial Centroid
    for i in range(no_of_clusters):
        centroids[i] = data[random_indexes[i]]
        
    print(f"Initialized Random Centroids =\n{centroids}")
    print(divider)
    
    return centroids

In [140]:
def get_euclidean_distance(vector1, vector2):
    return np.linalg.norm (vector1 - vector2)

## How get_vectorized_euclidean_distance computes the Euclidean distance between each pair of point and center

Let's say you have two arrays: data and centroids. Data has shape $(2, 2)$, which means it has 2 points with 2 features each. Centroids has shape $(3, 2)$, which means it has 3 cluster centers with 2 features each. You can write these arrays as matrices:

$$
\text{data} = \begin{bmatrix}
1 & 2 \\
3 & 4
\end{bmatrix}
$$

$$
\text{centroids} = \begin{bmatrix}
5 & 6 \\
7 & 8 \\
9 & 10
\end{bmatrix}
$$

You want to apply a vectorized function get_vectorized_euclidean_distance to these arrays, which computes the Euclidean distance between each pair of point and center. The output should be an array with shape $(2, 3)$, which contains the distances from each point to each center.

To do this, you need to use numpy broadcasting to expand data and centroids so that they have compatible shapes for get_vectorized_euclidean_distance. You do this by adding new axes to data and centroids using None or np.newaxis as index slices. This is a way of telling numpy that you want to add a new dimension to the array without changing its values.

Data[:, None, :] adds a new axis in the middle of data, making it a 3-D array with shape $(2, 1, 2)$. This means that the original data array is repeated along the new axis once. You can think of it as stacking two copies of data on top of each other. You can write this array as a tensor:

$$
\text{data}[:, \text{None}, :] = \begin{bmatrix}
\begin{bmatrix}
1 & 2
\end{bmatrix} \\
\begin{bmatrix}
3 & 4
\end{bmatrix}
\end{bmatrix}
$$

Centroids[None, :, :] adds a new axis at the beginning of centroids, making it a 3-D array with shape $(1, 3, 2)$. This means that the original centroids array is repeated along the new axis once. You can think of it as stacking one copy of centroids on top of itself. You can write this array as a tensor:

$$
\text{centroids}[\text{None}, :, :] = \begin{bmatrix}
\begin{bmatrix}
5 & 6 \\
7 & 8 \\
9 & 10
\end{bmatrix}
\end{bmatrix}
$$

When these arrays are passed to get_vectorized_euclidean_distance, they are broadcasted to a 3-D array with shape $(2, 3, 2)$. This means that for each point in data, there are 3 corresponding centers in centroids. Numpy does this by expanding the smaller array along the mismatched dimension until it matches the larger one. In this case, data is expanded along the second dimension from 1 to 3, and centroids is expanded along the first dimension from 1 to 2. You can think of it as creating a grid of points and centers, where each row corresponds to a point and each column corresponds to a center. You can write this array as a tensor:

$$
\text{get_vectorized_euclidean_distance}(\text{data}[:, \text{None}, :], \text{centroids}[\text{None}, :, :]) = \begin{bmatrix}
\begin{bmatrix}
1 & 2 \\
5 & 6
\end{bmatrix} &
\begin{bmatrix}
1 & 2 \\
7 & 8
\end{bmatrix} &
\begin{bmatrix}
1 & 2 \\
9 & 10
\end{bmatrix} \\

\begin{bmatrix}
3 & 4 \\
5 & 6
\end{bmatrix} &
\begin{bmatrix}
3 & 4 \\
7 & 8
\end{bmatrix} &
\begin{bmatrix}
3 & 4 \\
9 & 10
\end{bmatrix}

\end{bmatrix}
$$

Vfunc then computes the Euclidean distance between each pair of point and center, and returns a 2-D array with shape $(2, 3)$. This array contains the distances from each point to each center. You can think of it as flattening the grid of distances into a matrix. You can write this array as a matrix:

$$
\text{distances} = \begin{bmatrix}
d_{11} & d_{12} & d_{13} \\
d_{21} & d_{22} & d_{23}
\end{bmatrix}
$$

where $d_{ij}$ is the Euclidean distance between the $i$-th point and the $j$-th center, calculated by the formula:

$$
d_{ij} = \sqrt{(x_i - c_j)^2 + (y_i - c_j)^2}
$$

where $x_i$ and $y_i$ are the features of the $i$-th point, and $c_j$ and $c_j$ are the features of the $j$-th center.

For example, to calculate $d_{11}$, we use the formula:

$$
d_{11} = \sqrt{(1 - 5)^2 + (2 - 6)^2} = \sqrt{32} \approx 5.66
$$

Similarly, we can calculate the other distances and fill in the matrix. The final result is:

$$
\text{distances} = \begin{bmatrix}
5.66 & 8.49 & 11.31 \\
2.83 & 5.66 & 8.49
\end{bmatrix}
$$

In [4]:
def pairwise_distances_argmin_min (data, centroids):
    # vectorize the function
    get_vectorized_euclidean_distance = np.vectorize(get_euclidean_distance, signature='(n),(n)->()')
    
    # apply the vectorized function to the arrays
    distances = get_vectorized_euclidean_distance(data[:, None, :], centroids[None, :, :])
    
    # find the index and the value of the minimum distance along the specified axis
    argmin = np.argmin(distances, axis=1)
    min = np.min(distances, axis=1)
    
    # return the index and the value of the minimum distance
    cluster_affiliation = argmin
    distances = min
    
    return cluster_affiliation, distances

KMeans Function


In [5]:
def kmeans(data, no_of_clusters, max_iterations):
    # Initializing cluster centers randomly
    centroids = data[np.random.choice(len(data), no_of_clusters)]

    # Initializing cluster affiliations randomly
    cluster_affiliation = np.random.randint(no_of_clusters, size=len(data))

    # Initializing previous sum of squared errors
    j_prev = np.inf
    j = 0
    db_idx = np.inf
    dunn_idx = 0
    
    for iteration in range(max_iterations):
        # Assigning each point to the closest cluster center
        cluster_affiliation, distances = pairwise_distances_argmin_min(data, centroids)

        # Recomputing cluster centers as the mean of each cluster
        centroids = np.array([data[cluster_affiliation == i].mean(axis=0) for i in range(no_of_clusters)])

        # Computing sum of squared errors
        j = np.sum(distances ** 2)

        db_idx = davies_bouldin_index(data, cluster_affiliation, centroids)
        dunn_idx = dunn_index(data, cluster_affiliation, centroids)
        
        print(f"Iteration {iteration}:")
        print(f"New Cluster Affiliations =\n{cluster_affiliation}")
        print(f"Davies-Bouldin Index = {db_idx}")
        print(f"Dunn Index = {dunn_idx}")
        print(f"|J - J_prev| = {abs(j - j_prev)}")
        print(divider)

        # Checking convergence criterion
        if abs(j - j_prev) <= 10**(-5):
            break

        # Update previous sum of squared errors
        j_prev = j
    
    print(divider)
    print(f"Final Centroids =\n{centroids}")
    print(f"Final Cluster Affiliations =\n{cluster_affiliation}")
    print(f"J = {j}")
    print(f"Final Davies-Bouldin Index = {db_idx}")
    print(f"Final Dunn Index = {dunn_idx}")
    
    return centroids, cluster_affiliation

In [143]:
def create_image_from_point (centroid):
    image = px.imshow (centroid.reshape((28, 28)), binary_string = True)
    return image

In [144]:
no_of_clusters = 10                                                   # K clusters
no_of_training_data = 5000

print(f"Number of clusters = {no_of_clusters}")

# Setting file paths based on added MNIST Datasets
input_path = 'mnist/'
training_images_filepath = join(input_path, 'train-images-idx3-ubyte/train-images-idx3-ubyte')
training_labels_filepath = join(input_path, 'train-labels-idx1-ubyte/train-labels-idx1-ubyte')
test_images_filepath     = join(input_path, 't10k-images-idx3-ubyte/t10k-images-idx3-ubyte')
test_labels_filepath     = join(input_path, 't10k-labels-idx1-ubyte/t10k-labels-idx1-ubyte')

# Loading MINST dataset
mnist_dataloader = MnistDataloader(training_images_filepath, training_labels_filepath, test_images_filepath, test_labels_filepath)

(train_images, train_labels), (test_images, test_labels) = mnist_dataloader.load_data()

train_images, train_labels = train_images[:no_of_training_data], train_labels[:no_of_training_data]
normalized_train_images = train_images / 255

print(f"Length of train set = {len(normalized_train_images)}")
print(f"Length of test set = {len(test_images)}")

dimension_of_data = np.size(normalized_train_images, 1)                                                             # number of  data dimension in the data

print(f"Dimensions being used = {dimension_of_data}")
print(divider)

normalized_centroids, cluster_affiliation = kmeans(normalized_train_images, no_of_clusters, 500)
centroids = normalized_centroids * 255

purity = purity_score(train_labels, cluster_affiliation)
rand_idx = rand_index(train_labels, cluster_affiliation)

print(f"Purity = {purity}")
print(f"Rand Index = {rand_idx}")

			

Number of clusters = 10
Length of train set = 5000
Length of test set = 10000
Dimensions being used = 784
--------------------------------------------------------------------------------------


C:\Users\mirshafayat.ahmed\AppData\Local\Temp\ipykernel_35496\1183376977.py:14: RuntimeWarning:

divide by zero encountered in divide



Iteration 0:
New Cluster Affiliations =
[9 9 0 ... 4 7 0]
Davies-Bouldin Index = 3.451244613401471
Dunn Index = 0.2841784027373939
|J - J_prev| = inf
--------------------------------------------------------------------------------------
Iteration 1:
New Cluster Affiliations =
[9 9 8 ... 4 7 5]
Davies-Bouldin Index = 3.076300649210904
Dunn Index = 0.35354889667500156
|J - J_prev| = 141434.36140335375
--------------------------------------------------------------------------------------
Iteration 2:
New Cluster Affiliations =
[9 1 3 ... 4 7 4]
Davies-Bouldin Index = 3.0018911828896853
Dunn Index = 0.3587431577821984
|J - J_prev| = 8091.764085121744
--------------------------------------------------------------------------------------
Iteration 3:
New Cluster Affiliations =
[9 1 3 ... 4 7 4]
Davies-Bouldin Index = 2.965852543485874
Dunn Index = 0.3687932467384061
|J - J_prev| = 2464.981238309294
--------------------------------------------------------------------------------------
Iterati

In [145]:
from plotly.subplots import make_subplots
no_of_columns = 5
fig = \
    make_subplots(
        rows = len(normalized_centroids) // no_of_columns,
        cols = no_of_columns,
        horizontal_spacing = 0.1,
        vertical_spacing = 0.1
    )

for i in range(no_of_clusters):
    fig.add_trace((create_image_from_point (normalized_centroids[i])).data[0], row =(i // no_of_columns) + 1, col =i % no_of_columns + 1)
    
fig.show()

In [159]:
from sklearn.manifold import TSNE
import plotly.graph_objects as go

def make_3d_tsne_plot (train_images, train_labels,  centroids):
    pixel_columns  = [ 'pixel '+str(i) for i in range(len(train_images[0])) ]   # Creating column headers for each element of the pixel color vector
    df             = pd.DataFrame(train_images, columns = pixel_columns)                      # Creating a dataframe that would hold the data.
    row, col       = df.shape
    df['label']    = train_labels                                            # Creating a column named "label" for later use in coloring/labeling the datapoints

    display(df)
    
    centroid_df = pd.DataFrame(centroids, columns = pixel_columns)       # Creating a df that will only store centroid data but has the same structure as the original df

    centroid_df['label'] = ["centroid"] * no_of_clusters          # Setting the "label" as "centroid" for all centroids
    
    df_with_centroids        = pd.concat([df, centroid_df])                   # making a df with the original and centroid df
    df_with_centroids_subset = df_with_centroids[pixel_columns]
    
    tsne         = TSNE(n_components=3, verbose=1, perplexity=40, n_iter=300)
    tsne_results = tsne.fit_transform(df_with_centroids_subset)
    
    df_with_centroids['t-SNE-comp-1'] = tsne_results[:,0]          # Creating 3 columns to store the results of the three components
    df_with_centroids['t-SNE-comp-2'] = tsne_results[:,1]
    df_with_centroids['t-SNE-comp-3'] = tsne_results[:,2]

    prev_data     =  df_with_centroids.iloc[:-no_of_clusters]      # Separating out the Centroid and Original data so that they can be shown properly in the graph...
    centroid_data = df_with_centroids.iloc[-no_of_clusters:]

    fig = px.scatter_3d(
        prev_data,                   # df of Original Data
        x = prev_data['t-SNE-comp-1'],
        y = prev_data['t-SNE-comp-2'],
        z = prev_data['t-SNE-comp-3'],
        color='label',              # Assigning separate colors for different "label" value
        opacity=0.2,
        width=1200, height=800,     # Size of the output graph
    )
    fig.update_traces(              # changing the size of the markers
        marker=dict(
            size=4,
        ),
        selector=dict(mode='markers'))
    
    fig.add_trace(                              # Now adding the centroid tsne results data
        go.Scatter3d(
            x = centroid_data['t-SNE-comp-1'],
            y = centroid_data['t-SNE-comp-2'],
            z = centroid_data['t-SNE-comp-3'],
            mode='markers',
            marker=dict(
                size=12,
                color="black"
            ),
            name= 'Centroids',
    
        )
    )
    
    return fig

    

In [160]:
tsne_3d_plot = make_3d_tsne_plot (train_images, train_labels, centroids)
tsne_3d_plot.show()

pixel 0  pixel 1  pixel 2  pixel 3  pixel 4  pixel 5  pixel 6  pixel 7  \
0           0        0        0        0        0        0        0        0   
1           0        0        0        0        0        0        0        0   
2           0        0        0        0        0        0        0        0   
3           0        0        0        0        0        0        0        0   
4           0        0        0        0        0        0        0        0   
5           0        0        0        0        0        0        0        0   
6           0        0        0        0        0        0        0        0   
7           0        0        0        0        0        0        0        0   
8           0        0        0        0        0        0        0        0   
9           0        0        0        0        0        0        0        0   
10          0        0        0        0        0        0        0        0   
11          0        0        0        0        0        0        0        0   
12          0        0        0        0        0        0        0        0   
13          0        0        0        0        0        0        0        0   
14          0        0        0        0        0        0        0        0   
15          0        0        0        0        0        0        0        0   
16          0        0        0        0        0        0        0        0   
17          0        0        0        0        0        0        0        0   
18          0        0        0        0        0        0        0        0   
19          0        0        0        0        0        0        0        0   
20          0        0        0        0        0        0        0        0   
21          0        0        0        0        0        0        0        0   
22          0        0        0        0        0        0        0        0   
23          0        0        0        0        0        0        0        0   
24          0        0        0        0        0        0        0        0   
25          0        0        0        0        0        0        0        0   
26          0        0        0        0        0        0        0        0   
27          0        0        0        0        0        0        0        0   
28          0        0        0        0        0        0        0        0   
29          0        0        0        0        0        0        0        0   
30          0        0        0        0        0        0        0        0   
31          0        0        0        0        0        0        0        0   
32          0        0        0        0        0        0        0        0   
33          0        0        0        0        0        0        0        0   
34          0        0        0        0        0        0        0        0   
35          0        0        0        0        0        0        0        0   
36          0        0        0        0        0        0        0        0   
37          0        0        0        0        0        0        0        0   
38          0        0        0        0        0        0        0        0   
39          0        0        0        0        0        0        0        0   
40          0        0        0        0        0        0        0        0   
41          0        0        0        0        0        0        0        0   
42          0        0        0        0        0        0        0        0   
43          0        0        0        0        0        0        0        0   
44          0        0        0        0        0        0        0        0   
45          0        0        0        0        0        0        0        0   
46          0        0        0        0        0        0        0        0   
47          0        0        0        0        0        0        0        0   
48          0        0        0        0        0        0        0        0   
49    

[t-SNE] Computing 121 nearest neighbors...
[t-SNE] Indexed 5010 samples in 0.004s...
[t-SNE] Computed neighbors for 5010 samples in 1.015s...
[t-SNE] Computed conditional probabilities for sample 1000 / 5010
[t-SNE] Computed conditional probabilities for sample 2000 / 5010
[t-SNE] Computed conditional probabilities for sample 3000 / 5010
[t-SNE] Computed conditional probabilities for sample 4000 / 5010
[t-SNE] Computed conditional probabilities for sample 5000 / 5010
[t-SNE] Computed conditional probabilities for sample 5010 / 5010
[t-SNE] Mean sigma: 594.440027
[t-SNE] KL divergence after 250 iterations with early exaggeration: 80.464020
[t-SNE] KL divergence after 300 iterations: 2.026351


# Reddit Data

In [10]:
from nltk.tokenize import word_tokenize
import nltk
from nltk.stem.porter import PorterStemmer
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\mirshafayat.ahmed\AppData\Roaming\nltk_data..
[nltk_data]     .
[nltk_data]   Package punkt is already up-to-date!


True

In [14]:
def load_reddit_dataset (reddit_dataset_path, column_names):
    dataset = \
        pd.read_csv (
            reddit_dataset_path,
            names = column_names,
            header = 0
        )

    data = dataset[[column_names[0], column_names[1], column_names[3], column_names[4]]]
    topic = dataset[column_names[2]]

    return data, topic

def stem_tokens(tokens):
    stemmer = PorterStemmer()
    stemmed = []
    for item in tokens:
        stemmed.append(stemmer.stem(item))
    return stemmed

In [17]:
column_names = [
    "parent_id",
    "text",
    "topic",
    "length",
    "size_range"
]

reddit_dataset_path = "reddit_comments/reddit_data.csv"
reddit_data, topic = load_reddit_dataset (reddit_dataset_path, column_names)

reddit_data[column_names[1]] = reddit_data[column_names[1]].map(str)
reddit_data[column_names[1]] = reddit_data[column_names[1]].map(word_tokenize)
reddit_data[column_names[1]] = reddit_data[column_names[1]].map(stem_tokens)

print (reddit_data[column_names[1]])


0        [thank, !, not, sure, if, those, link, were, u...
1        [i, think, it, unlik, someon, would, kill, the...
2        [hoult, is, anoth, one, that, 's, import, ., b...
3        [can, have, my, opinion, ., they, 're, noisi, ...
4        [nice, !, that, remind, me, of, a, more, recen...
5        [wa, briefli, consid, a, top, lineback, and, t...
6        [i, 'd, prefer, 4-5-6-4-5-6, honestli, you, do...
7        [i, like, a, corner, who, will, get, in, there...
8        [just, ani, titl, that, doe, n't, use, gamewor...
9        [becaus, be, black, skin, as, a, neg, is, a, r...
10       [i, think, the, first, thing, you, need, to, d...
11       [unless, you, mean, befor, bradi, wa, in, the,...
12       [jordan, dropsthrow, and, call, the, titan, ir...
13       [i, 'd, like, that, :, ), i, creep, a, littl, ...
14       [evga, are, a, great, brand, for, psu, ,, i, w...
15       [i, would, n't, recommend, come, in, contact, ...
16       [i, never, talk, about, their, career, ,, mere.